In [10]:
# directory path setting
vital_files_directory = 'presets_vital'  # Replace with the actual directory path
json_files_directory = 'presets_json'    # Replace with the desired directory for JSON files
data_directory = 'misc'
metadata_directory = 'metadata'
model_directory = 'models'
output_directory = 'presets_synthesized'
samples_wavetables_path = 'misc/full_samples_and_wavetables.json'
default_values_path = 'misc/default_values.json'


## Preprocessing: Vital Files to Dataframe (X)

In [2]:
from collections import defaultdict
from pathlib import Path

import numpy as np
import zipfile
import os
import json
import pandas as pd
import sdv
import shutil
import matplotlib.pyplot as plt
import heapq
import time
import pickle
import math
import re
import inspect

from sdv.single_table import GaussianCopulaSynthesizer
from sdv.metadata import SingleTableMetadata


# 모든 column 표시하도록 설정
pd.set_option('display.max_columns', None)

In [9]:
# Create the directory for JSON files if it doesn't exist
os.makedirs(json_files_directory, exist_ok=True)

# Function to copy .vital files as .json and count the number of copied files
def copy_and_rename_vital_to_json(source_directory, destination_directory):
    copied_count = 0
    for filename in os.listdir(source_directory):
        if filename.endswith('.vital'):
            # Construct full file paths
            vital_file = os.path.join(source_directory, filename)
            json_file = os.path.join(destination_directory, filename.replace('.vital', '.json'))
            # Copy and rename the file
            shutil.copy2(vital_file, json_file)
            copied_count += 1
    print(f'{copied_count} Vital files copied and renamed to JSON')

# Run the copy and renaming function
copy_and_rename_vital_to_json(vital_files_directory, json_files_directory)


0 Vital files copied and renamed to JSON


In [127]:
# 깨진파일삭제

def is_valid_json(file_path):
    try:
        with open(file_path, 'r') as file:
            json.load(file)
        return True
    except (ValueError, json.JSONDecodeError):
        return False

def delete_invalid_json_files(directory):
    for filename in os.listdir(directory):
        file_path = os.path.join(directory, filename)
        if filename.endswith('.json') and not is_valid_json(file_path):
            print(f"Deleting invalid JSON file: {filename}")
            os.remove(file_path)


delete_invalid_json_files(json_files_directory)


Deleting invalid JSON file: Accordeon.json
Deleting invalid JSON file: Action_Pluck.json
Deleting invalid JSON file: Press_Start.json
Deleting invalid JSON file: Start_Synthezising.json


In [128]:
#add actual file name

def add_filename_to_json(directory_path):
    for filename in os.listdir(directory_path):
        if filename.endswith(".json"):
            file_path = os.path.join(directory_path, filename)
            with open(file_path, 'r') as f:
                try:
                    data = json.load(f)
                except:
                    print ("Can't decode json for " + filename)
                    continue

            # Extract the file name without the extension
            file_name_without_ext = os.path.splitext(filename)[0]

            # Add the file name to the beginning of the JSON data
            data = {"file_name": file_name_without_ext, **data} 

            with open(file_path, 'w') as f:
                json.dump(data, f, indent=4)

# Example usage
add_filename_to_json(json_files_directory)

In [129]:
# Custom_warps 삭제

def remove_custom_warps_from_jsons(extract_path):
    # Iterate over all files in the specified directory
    for filename in os.listdir(extract_path):
        if filename.endswith(".json"):  # Only process JSON files
            file_path = os.path.join(extract_path, filename)
            with open(file_path, 'r') as file:
                data = json.load(file)

            # Check if 'settings' exists and 'custom_warps' is nested within it
            if 'settings' in data and 'custom_warps' in data['settings']:
                del data['settings']['custom_warps']

                # Write the updated JSON back to the file
                with open(file_path, 'w') as file:
                    json.dump(data, file, indent=4)

# Example usage
remove_custom_warps_from_jsons(json_files_directory)

In [130]:
# num_points n개 이상인 파일이 nn퍼센트 넘으면 파일 삭제 (상황에 따라 셀 하단에서 수치 조절할 것)

def find_max_num_points(data):
    """
    Recursively searches for the 'num_points' key in a JSON object and returns the maximum value found.
    If 'num_points' is not found, returns None.
    """
    max_value = None

    if isinstance(data, dict):
        for key, value in data.items():
            if key == 'num_points':
                max_value = value if max_value is None else max(max_value, value)
            else:
                found = find_max_num_points(value)
                if found is not None:
                    max_value = found if max_value is None else max(max_value, found)
    elif isinstance(data, list):
        for item in data:
            found = find_max_num_points(item)
            if found is not None:
                max_value = found if max_value is None else max(max_value, found)

    return max_value

def count_and_delete_jsons(extract_path, threshold_value=50, delete_threshold_percent=10):
    json_files = list(Path(extract_path).rglob('*.json'))
    total_files = len(json_files)
    if total_files == 0:
        print("No JSON files found.")
        return

    files_with_high_points = []

    # Traverse all JSON files
    for json_file in json_files:
        with open(json_file, 'r') as file:
            try:
                data = json.load(file)
                max_num_points = find_max_num_points(data)
                if max_num_points is not None and max_num_points > threshold_value:
                    files_with_high_points.append(json_file)
            except json.JSONDecodeError:
                print(f"Error decoding JSON file: {json_file}")

    high_points_count = len(files_with_high_points)
    target_percent = (high_points_count / total_files) * 100

    print(f"Total JSON files: {total_files}")
    print(f"Files with 'num_points' max > {threshold_value}: {high_points_count}")
    print(f"Percentage of target files: {target_percent:.2f}%")

    # Check if the count is less than delete_threshold_percent of total files
    if target_percent < delete_threshold_percent:
        print(f"Deleting {high_points_count} files with 'num_points' max > {threshold_value}...")
        for file_path in files_with_high_points:
            try:
                os.remove(file_path)
                print(f"Deleted: {file_path}")
            except OSError as e:
                print(f"Error deleting file {file_path}: {e}")
    else:
        print(f"No files deleted as the percentage is above {delete_threshold_percent}% threshold.")

# Example usage:
count_and_delete_jsons(json_files_directory, threshold_value=19, delete_threshold_percent=10)


Total JSON files: 4317
Files with 'num_points' max > 19: 410
Percentage of target files: 9.50%
Deleting 410 files with 'num_points' max > 19...
Deleted: C:\Users\SKT012\project\data\presets_json\1XXX.json
Deleted: C:\Users\SKT012\project\data\presets_json\1_Key_3_Oscillators.json
Deleted: C:\Users\SKT012\project\data\presets_json\4HarderStyles.json
Deleted: C:\Users\SKT012\project\data\presets_json\55_Steps_Bass.json
Deleted: C:\Users\SKT012\project\data\presets_json\8BIT_DRIP.json
Deleted: C:\Users\SKT012\project\data\presets_json\8bit_Lead_1.json
Deleted: C:\Users\SKT012\project\data\presets_json\8_bit_Retracted_Punch.json
Deleted: C:\Users\SKT012\project\data\presets_json\ACID_Blood_Is_Pumpin.json
Deleted: C:\Users\SKT012\project\data\presets_json\ACID_Bluish.json
Deleted: C:\Users\SKT012\project\data\presets_json\ACID_Bro.json
Deleted: C:\Users\SKT012\project\data\presets_json\ACID_Bro2.json
Deleted: C:\Users\SKT012\project\data\presets_json\ACID_Cybertripping_1.json
Deleted: C:\Us

In [131]:
# Settings-Modulations에 빈 값들 삭제

def clean_modulations(file_path):
    with open(file_path, 'r') as file:
        data = json.load(file)

    if "settings" in data and "modulations" in data["settings"]:
        modulations = data["settings"]["modulations"]
        cleaned_modulations = [
            mod for mod in modulations
            if mod.get("destination") and mod.get("source")
        ]
        data["settings"]["modulations"] = cleaned_modulations

        with open(file_path, 'w') as file:
            json.dump(data, file, indent=4)

def process_json_files(directory_path):
    for filename in os.listdir(directory_path):
        if filename.endswith(".json"):
            file_path = os.path.join(directory_path, filename)
            clean_modulations(file_path)


process_json_files(json_files_directory)

In [132]:
# Settings-Sample, Wavetables에 긴 문자열들 제거하고 Name만 남기기

def modify_json_files(extract_path):
    # Iterate over all files in the specified directory
    for filename in os.listdir(extract_path):
        if filename.endswith('.json'):
            file_path = os.path.join(extract_path, filename)
            with open(file_path, 'r') as file:
                data = json.load(file)

            # Check if 'settings' and 'sample' keys exist
            if 'settings' in data:
                if 'sample' in data['settings']:
                    # Retain only the 'name' key in 'sample'
                    if 'name' in data['settings']['sample']:
                        data['settings']['sample'] = {'name': data['settings']['sample']['name']}

                # Check if 'wavetables' key exists in 'settings'
                if 'wavetables' in data['settings']:
                    # Retain only the 'name' key in each dictionary within 'wavetables' list
                    updated_wavetables = []
                    for entry in data['settings']['wavetables']:
                        if 'name' in entry:
                            updated_wavetables.append({'name': entry['name']})
                    data['settings']['wavetables'] = updated_wavetables

            # Write the modified data back to the JSON file
            with open(file_path, 'w') as file:
                json.dump(data, file, indent=4)


modify_json_files(json_files_directory)


In [133]:
# 미사용 Osc, Sample(osc_on, sample_on=0.0)의 Name 변경

def update_json_files(path):
    for filename in os.listdir(path):
        if filename.endswith(".json"):
            file_path = os.path.join(path, filename)
            with open(file_path, 'r') as file:
                data = json.load(file)

            # Check and update the "settings" values
            if 'settings' in data:
                settings = data['settings']

                # Check osc_1_on value
                if settings.get('osc_1_on', None) == 0.0:
                    if 'wavetables' in settings and len(settings['wavetables']) > 0:
                        settings['wavetables'][0]['name'] = 'osc_off'

                # Check osc_2_on value
                if settings.get('osc_2_on', None) == 0.0:
                    if 'wavetables' in settings and len(settings['wavetables']) > 1:
                        settings['wavetables'][1]['name'] = 'osc_off'

                # Check osc_3_on value
                if settings.get('osc_3_on', None) == 0.0:
                    if 'wavetables' in settings and len(settings['wavetables']) > 2:
                        settings['wavetables'][2]['name'] = 'osc_off'

                # Check sample_on value
                if settings.get('sample_on', None) == 0.0:
                    if 'sample' in settings and 'name' in settings['sample']:
                        settings['sample']['name'] = 'sample_off'

            # Write the updated data back to the file
            with open(file_path, 'w') as file:
                json.dump(data, file, indent=4)


update_json_files(json_files_directory)

In [134]:
# creating dataframe

# Function to flatten nested JSON
def flatten_json(y, prefix=''):
    out = {}

    def flatten(x, name=''):
        if type(x) is dict:
            for a in x:
                flatten(x[a], name + a + '-')
        elif type(x) is list:
            i = 0
            for a in x:
                flatten(a, name + str(i) + '-')
                i += 1
        else:
            out[name[:-1]] = x

    flatten(y)
    return out


# List to hold all flattened data
all_flat_data = []

# Iterating through all JSON files in the directory
for filename in os.listdir(json_files_directory):
    if filename.endswith('.json'):
        file_path = os.path.join(json_files_directory, filename)

        # Read the JSON file
        with open(file_path, 'r') as file:
            data = json.load(file)

        # Flatten the JSON data
        flat_data = flatten_json(data)

        # Add to the list of all flattened data
        all_flat_data.append(flat_data)

# Convert the list of dictionaries to a DataFrame
df = pd.DataFrame(all_flat_data)

# Convert DataFrame to dictionary with native Python data types
flat_data_converted = df.astype(object).where(pd.notnull(df), None).to_dict(orient='records')

In [135]:
df.shape

(3907, 2642)

In [136]:
# Dropping the specified columns from the DataFrame
df = df.drop(columns=['author', 'comments', 'macro1', 'macro2', 'macro3', 'macro4'])

In [137]:
csv_file_path = os.path.join(data_directory, 'Matched_Preset_Labels.csv')  # Replace with your actual file path

# Read the CSV file into a pandas DataFrame
df_label = pd.read_csv(csv_file_path)
df = pd.merge(df, df_label, on='file_name', how='left')
df = df[['genre', 'sound_type'] + [col for col in df.columns if col not in ['genre', 'sound_type']]]


In [138]:
# points의 xy좌표 양끝으로 퍼트리는 식으로 재배치(x>0.5기준으로) (약 6분 걸림)

# Function to process each group
def process_group(group):
    # Separate X and Y pairs
    x_cols = group.columns[::2]
    y_cols = group.columns[1::2]

    for idx, row in group.iterrows():
        # Extract X and Y values
        x_values = row[x_cols].values
        y_values = row[y_cols].values

        # Pair them up and sort by X
        xy_pairs = [(x, y) for x, y in zip(x_values, y_values)]
        xy_pairs.sort(key=lambda pair: pair[0])

        # Split and move (X, Y) pairs with X > 0.5 to the right
        left_pairs = [(x, y) for x, y in xy_pairs if x <= 0.5 or np.isnan(x)]
        right_pairs = [(x, y) for x, y in xy_pairs if x > 0.5]

        # Combine the pairs and handle NaNs
        final_pairs = left_pairs + right_pairs
        for i, (x, y) in enumerate(final_pairs):
            group.iloc[idx, i * 2] = x
            group.iloc[idx, i * 2 + 1] = y

    return group

# Identify the groups and process each one
grouped = df.columns.str.extract(r'(.*)-points-')[0]
for group_name in grouped.unique():
    group_cols = df.columns[grouped == group_name]
    df[group_cols] = process_group(df[group_cols])

df.head()


genre sound_type           file_name         preset_name preset_style  \
0   Synthwave      Synth            0802_Sly            0802_Sly         Keys   
1  Multigenre       Keys         1001_Nights         1001_Nights         Keys   
2     Dubstep       Bass  100NoModernTalking  100NoModernTalking         Bass   
3    Halfstep      Reese      100RACKS_REESE                 NaN         Bass   
4   Cinematic        Pad         10K_STRINGS                 NaN          Pad   

   settings-beats_per_minute  settings-bypass  settings-chorus_cutoff  \
0                   1.650000              0.0               89.170738   
1                   2.166667              0.0               60.000000   
2                   2.000000              0.0               93.243370   
3                   1.450000              0.0              105.500000   
4                   2.000000              0.0               60.000000   

   settings-chorus_delay_1  settings-chorus_delay_2  settings-chorus_dry_wet  \
0                -9.000000                -7.000000                  0.10500   
1                -9.000000                -7.000000                  0.50000   
2                -8.613684                -5.951427                  0.24662   
3                -7.584501                -6.506352                  0.40000   
4                -9.000000                -7.000000                  0.00000   

   settings-chorus_feedback  settings-chorus_frequency  \
0                  0.104500                       -6.0   
1                  0.400000                       -3.0   
2                  0.255573                       -3.0   
3                  0.150000                       -3.0   
4                  0.400000                       -3.0   

   settings-chorus_mod_depth  settings-chorus_on  settings-chorus_spread  \
0                   0.735000                 1.0                0.000000   
1                   0.500000                 0.0                1.000000   
2                   0.519004                 1.0                0.265199   
3                   0.470000                 1.0                0.093125   
4                   0.500000                 0.0                1.000000   

   settings-chorus_sync  settings-chorus_tempo  settings-chorus_voices  \
0                   0.0                    4.0                     4.0   
1                   1.0                    4.0                     4.0   
2                   1.0                    5.0                     4.0   
3                   1.0                    0.0                     4.0   
4                   1.0                    4.0                     4.0   

   settings-compressor_attack  settings-compressor_band_gain  \
0                    0.500000                           11.7   
1                    0.500000                           11.7   
2                    0.753379                           11.7   
3                    0.500000                           11.7   
4                    0.500000                           11.7   

   settings-compressor_band_lower_ratio  \
0                              0.800000   
1                              0.800000   
2                              0.872181   
3                              0.800000   
4                              0.800000   

   settings-compressor_band_lower_threshold  \
0                                -36.000000   
1                                -36.000000   
2                                -27.578941   
3                                -36.000000   
4                                -36.000000   

   settings-compressor_band_upper_ratio  \
0                                 0.857   
1                                 0.857   
2                                 0.857   
3                                 0.857   
4                                 0.857   

   settings-compressor_band_upper_threshold  \
0                                     -25.0   
1                                     -25.0   
2                      

In [139]:
df.replace("", np.nan, inplace=True) # ""값 모두 NaN으로 바꾸기(""는 CTGAN이 학습 불가)

# (추가) 필요없는 Remap 좌표 name(Triangle, Saw Down 등) 모두 NaN으로 변경
# Define the patterns you want to match
patterns = [
    "settings-custom_warps-",
    "settings-lfos-",
    "settings-modulations-"
]

# Iterate through the columns and replace values with NaN for matching columns
for col in df.columns:
    if any(col.startswith(pattern) and col.endswith('-name') for pattern in patterns):
        df[col] = np.nan


In [140]:
# 안쓰는 애들 값은 NaN으로 만들어서 학습하지 않도록 처리

osc_smp_filter_fx = [
    "osc_1", "osc_2", "osc_3", "sample", "filter_1", "filter_2", "filter_fx",
    "chorus", "compressor", "delay", "distortion", "eq", "flanger", "phaser", "reverb"
]

lfo_env_rand = [
    "lfo_1", "lfo_2", "lfo_3", "lfo_4", "lfo_5", "lfo_6", "lfo_7", "lfo_8",
    "env_1", "env_2", "env_3", "env_4", "env_5", "env_6",
    "random_1", "random_2", "random_3", "random_4"
]

def process_row(row):
    # Process osc_smp_filter_fx conditions
    for name in osc_smp_filter_fx:
        on_col = f"{name}_on"
        if on_col in row.index and row[on_col] == 0.0:
            for col in row.index:
                if col != on_col and name in col:
                    row[col] = np.nan

    # Process sample_on condition
    if "sample_on" in row.index and row["sample_on"] == 0.0:
        for col in row.index:
            if col != "sample_on" and "sample_" in col:
                row[col] = np.nan

    # Process lfo_env_rand condition
    if not any(row[col] for col in lfo_env_rand if col in row.index):
        for col in row.index:
            if any(lfo_env_rand_name in col for lfo_env_rand_name in lfo_env_rand):
                row[col] = np.nan

    # Process LFO existence conditions
    for i in range(1, 9):
        lfo_name = f"lfo_{i}"
        if lfo_name not in row.index or pd.isna(row[lfo_name]) or row[lfo_name] == 0:
            lfos_num = i - 1
            lfos_col_pattern = f"lfos-{lfos_num}"
            for col in row.index:
                if lfos_col_pattern in col:
                    row[col] = np.nan

    return row

# Apply the processing function to each row in the DataFrame
df = df.apply(process_row, axis=1)


In [141]:
# perset name generalization

# Function to rename the 'preset_name' column with unique preset names
def rename_presets(column):
    new_names = [f"preset_name_{i+1}" for i in range(len(column))]
    return new_names

# Apply the function to the 'preset_name' column
df['preset_name'] = rename_presets(df['preset_name'])
df = df.drop('file_name', axis=1)

In [172]:
#save preprocessed file
file_path = r'C:\Users\SKT012\project\data\filename.csv'
os.makedirs(os.path.dirname(file_path), exist_ok=True)

df.to_csv(file_path, index=False)

## 전처리된 코드 가지고 있을 경우:

In [12]:
processed_path = 'data/preprocessed_preset_240814.csv'
df = pd.read_csv(processed_path)
df.head()

C:\Users\SKT\AppData\Local\Temp\ipykernel_16020\3831002451.py:2: DtypeWarning: Columns (946,1264,1321,1378,1426,1435,1462,1489,1504,1519,1530,1531,1532,1533,1534,1535,1536,1537,1538,1539,1540,1541,1542,1543,1544,1545,1546,1547,1548,1549,1550,1551,1552,1553,1554,1555,1556,1557,1558,1559,1560,1561,1562,1563,1564,1565,1566,1567,1568,1569,1570,1571,1572,1573,1574,1575,1576,1577,1578,1579,1580,1581,1582,1583,1584,1585,1586,1587,1588,1589,1590,1591,1592,1593,1594,1595,1596,1597,1598,1599,1600,1601,1602,1603,1604,1605,1606,1607,1608,1609,1610,1611,1668,1677,1686,1698,1710,1722,1740,1779,1794,1851,1884,1914,1923,1938,1953,2004,2016,2115,2244,2259,2274,2322,2331,2332,2333,2348,2381,2459,2507,2549,2588,2603,2618) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(processed_path)


genre sound_type    preset_name preset_style  \
0   Synthwave      Synth  preset_name_1         Keys   
1  Multigenre       Keys  preset_name_2         Keys   
2     Dubstep       Bass  preset_name_3         Bass   
3    Halfstep      Reese  preset_name_4         Bass   
4   Cinematic        Pad  preset_name_5          Pad   

   settings-beats_per_minute  settings-bypass  settings-chorus_cutoff  \
0                   1.650000              0.0               89.170738   
1                   2.166667              0.0               60.000000   
2                   2.000000              0.0               93.243370   
3                   1.450000              0.0              105.500000   
4                   2.000000              0.0               60.000000   

   settings-chorus_delay_1  settings-chorus_delay_2  settings-chorus_dry_wet  \
0                -9.000000                -7.000000                  0.10500   
1                -9.000000                -7.000000                  0.50000   
2                -8.613684                -5.951427                  0.24662   
3                -7.584501                -6.506352                  0.40000   
4                -9.000000                -7.000000                  0.00000   

   settings-chorus_feedback  settings-chorus_frequency  \
0                  0.104500                       -6.0   
1                  0.400000                       -3.0   
2                  0.255573                       -3.0   
3                  0.150000                       -3.0   
4                  0.400000                       -3.0   

   settings-chorus_mod_depth  settings-chorus_on  settings-chorus_spread  \
0                   0.735000                 1.0                0.000000   
1                   0.500000                 0.0                1.000000   
2                   0.519004                 1.0                0.265199   
3                   0.470000                 1.0                0.093125   
4                   0.500000                 0.0                1.000000   

   settings-chorus_sync  settings-chorus_tempo  settings-chorus_voices  \
0                   0.0                    4.0                     4.0   
1                   1.0                    4.0                     4.0   
2                   1.0                    5.0                     4.0   
3                   1.0                    0.0                     4.0   
4                   1.0                    4.0                     4.0   

   settings-compressor_attack  settings-compressor_band_gain  \
0                    0.500000                           11.7   
1                    0.500000                           11.7   
2                    0.753379                           11.7   
3                    0.500000                           11.7   
4                    0.500000                           11.7   

   settings-compressor_band_lower_ratio  \
0                              0.800000   
1                              0.800000   
2                              0.872181   
3                              0.800000   
4                              0.800000   

   settings-compressor_band_lower_threshold  \
0                                -36.000000   
1                                -36.000000   
2                                -27.578941   
3                                -36.000000   
4                                -36.000000   

   settings-compressor_band_upper_ratio  \
0                                 0.857   
1                                 0.857   
2                                 0.857   
3                                 0.857   
4                                 0.857   

   settings-compressor_band_upper_threshold  \
0                                     -25.0   
1                                     -25.0   
2                                     -25.0   
3                                     -25.0   
4                                     -25.0   

   settings-compressor_enabled_

In [13]:
# Creating dfs for each genre and sound type

# Initialize dictionaries to hold the DataFrames
genre_dfs = {}
sound_type_dfs = {}

# Get unique values from the 'genre' and 'sound_type' columns
genres = df['genre'].unique()
sound_types = df['sound_type'].unique()

# Create separate DataFrames for each genre and store them in the dictionary
for genre in genres:
    genre_dfs[genre] = df[df['genre'] == genre]

# Create separate DataFrames for each sound type and store them in the dictionary
for sound_type in sound_types:
    sound_type_dfs[sound_type] = df[df['sound_type'] == sound_type]

## Single Dataframe Extraction (example)

In [14]:
# How to use 1

df_bass = sound_type_dfs['Bass']
df_bass.head()

genre sound_type    preset_name preset_style  \
2             Dubstep       Bass  preset_name_3         Bass   
5          Multigenre       Bass  preset_name_6         Bass   
6  Breakbeat / Breaks       Bass  preset_name_7         Bass   
7  Breakbeat / Breaks       Bass  preset_name_8         Bass   
8  Breakbeat / Breaks       Bass  preset_name_9         Bass   

   settings-beats_per_minute  settings-bypass  settings-chorus_cutoff  \
2                   2.000000              0.0               93.243370   
5                   2.333333              0.0               95.680000   
6                   2.200000              0.0              102.625542   
7                   2.200000              0.0              102.625542   
8                   2.200000              0.0               60.000000   

   settings-chorus_delay_1  settings-chorus_delay_2  settings-chorus_dry_wet  \
2                -8.613684                -5.951427                  0.24662   
5                -9.326710                -9.613684                  0.05500   
6                -8.825313                -8.415807                  0.09500   
7                -8.825313                -8.415807                  0.09500   
8                -9.000000                -7.000000                  0.50000   

   settings-chorus_feedback  settings-chorus_frequency  \
2                  0.255573                     -3.000   
5                  0.152000                     -3.225   
6                  0.390500                     -3.000   
7                  0.390500                     -3.000   
8                  0.400000                     -3.000   

   settings-chorus_mod_depth  settings-chorus_on  settings-chorus_spread  \
2                   0.519004                 1.0                0.265199   
5                   1.000000                 1.0                0.470000   
6                   0.406693                 1.0                0.327869   
7                   0.406693                 1.0                0.327869   
8                   0.500000                 0.0                1.000000   

   settings-chorus_sync  settings-chorus_tempo  settings-chorus_voices  \
2                   1.0                    5.0                     4.0   
5                   0.0                    4.0                     4.0   
6                   1.0                    4.0                     3.0   
7                   1.0                    4.0                     3.0   
8                   1.0                    4.0                     4.0   

   settings-compressor_attack  settings-compressor_band_gain  \
2                    0.753379                      11.700000   
5                    1.000000                      11.700000   
6                    0.598845                       5.192059   
7                    0.598845                       5.192059   
8                    0.578483                      15.170900   

   settings-compressor_band_lower_ratio  \
2                              0.872181   
5                              0.726028   
6                              0.118262   
7                              0.118262   
8                              0.264349   

   settings-compressor_band_lower_threshold  \
2                                -27.578941   
5                                -27.780834   
6                                -38.782608   
7                                -38.782608   
8                                -32.391235   

   settings-compressor_band_upper_ratio  \
2                                 0.857   
5                                 0.257   
6                                 0.857   
7                                 0.857   
8                                 0.857   

   settings-compressor_band_upper_threshold  \
2                                -25.000000   
5                                -23.945221   
6                                -21.521740   
7                                -21.521740   
8                                -30.56

In [20]:
# How to use 2
# Access the DataFrame for sound_type 'Bass' from the sound_type_dfs dictionary
df_bass = sound_type_dfs['Bass']

# Now filter df_bass for genre 'Dubstep'
df_bass_dubstep = df_bass[df_bass['genre'] == 'Dubstep']

# Display the filtered DataFrame
df_bass_dubstep.head()


genre sound_type      preset_name preset_style  \
2   Dubstep       Bass    preset_name_3         Bass   
24  Dubstep       Bass   preset_name_25         Bass   
75  Dubstep       Bass   preset_name_76         Bass   
79  Dubstep       Bass   preset_name_80         Bass   
99  Dubstep       Bass  preset_name_100         Bass   

    settings-beats_per_minute  settings-bypass  settings-chorus_cutoff  \
2                    2.000000              0.0                93.24337   
24                   2.166667              0.0                60.00000   
75                   2.666667              0.0                60.00000   
79                   2.000000              0.0                80.93792   
99                   2.500000              0.0                60.00000   

    settings-chorus_delay_1  settings-chorus_delay_2  settings-chorus_dry_wet  \
2                 -8.613684                -5.951427                  0.24662   
24                -9.000000                -7.000000                  0.50000   
75                -6.972483                -8.126860                  0.50000   
79                -9.000000                -7.000000                  0.11480   
99                -9.000000                -7.000000                  0.50000   

    settings-chorus_feedback  settings-chorus_frequency  \
2                   0.255573                       -3.0   
24                  0.400000                       -3.0   
75                  0.400000                       -3.0   
79                  0.400000                       -3.0   
99                  0.400000                       -3.0   

    settings-chorus_mod_depth  settings-chorus_on  settings-chorus_spread  \
2                    0.519004                 1.0                0.265199   
24                   0.500000                 0.0                1.000000   
75                   0.000000                 1.0                1.000000   
79                   0.500000                 0.0                0.000000   
99                   0.500000                 0.0                1.000000   

    settings-chorus_sync  settings-chorus_tempo  settings-chorus_voices  \
2                    1.0                    5.0                     4.0   
24                   1.0                    4.0                     4.0   
75                   1.0                    4.0                     4.0   
79                   1.0                    2.0                     4.0   
99                   1.0                    4.0                     4.0   

    settings-compressor_attack  settings-compressor_band_gain  \
2                     0.753379                           11.7   
24                    0.260000                           11.7   
75                    0.025000                           11.7   
79                    0.500000                           11.7   
99                    0.000000                           11.7   

    settings-compressor_band_lower_ratio  \
2                               0.872181   
24                              0.800000   
75                              0.800000   
79                              0.800000   
99                              0.800000   

    settings-compressor_band_lower_threshold  \
2                                 -27.578941   
24                                -56.162586   
75                                -38.795269   
79                                -39.000000   
99                                -53.219734   

    settings-compressor_band_upper_ratio  \
2                               0.857000   
24                              0.754561   
75                              0.771960   
79                              0.857000   
99                              0.857000   

    settings-compressor_band_upper_threshold  \
2                                 -25.000000   
24                                -33.455284   
75                                -22.417324   
79                                -24.000000   
99                

## Generating Synthesizer

In [144]:
def generate_synthesizer(df, name):
    metadata = generate_metadata(df, name)
    model = train_and_save_synthesizer(df, metadata, name)
    return model

In [145]:
def generate_metadata(df, name):
    # Create metadata object
    metadata = SingleTableMetadata()
    
    # Detect metadata from the DataFrame
    metadata.detect_from_dataframe(df)
    
    # Handle unknown columns if they exist
    unknown_columns = metadata.get_column_names(sdtype='unknown')
    if unknown_columns:
        metadata.update_columns(
            column_names=unknown_columns,
            sdtype='categorical'
        )
    
    # Optionally, set a primary key if needed
    # metadata.set_primary_key(column_name='preset_name')  # Uncomment and modify if you have a primary key
    
    # Validate the metadata
    metadata.validate()
    metadata.validate_data(data=df)
    
    # Construct the metadata filename using the DataFrame variable name
    metadata_filename = f'{name}_metadata.json'
    
    # Construct the full file path using the global metadata_directory
    full_file_path = os.path.join(metadata_directory, metadata_filename)
    
    # Save metadata to JSON in the specified directory
    metadata.save_to_json(filepath=full_file_path)

    # Return the metadata object
    return metadata


In [146]:
def train_and_save_synthesizer(df, metadata, name):
    
    # Step 1: Create the synthesizer
    synthesizer = GaussianCopulaSynthesizer(metadata)
    
    # Step 2: Train the synthesizer
    start_time = time.time()
    synthesizer.fit(df)
    end_time = time.time()
    
    # Calculate the time taken
    training_time = end_time - start_time
    
    # Convert the time to hours, minutes, and seconds
    hours, rem = divmod(training_time, 3600)
    minutes, seconds = divmod(rem, 60)
    
    # Display the formatted time
    print(f"Model training took {int(hours):02}:{int(minutes):02}:{int(seconds):02} (hh:mm:ss)")
    
    # Step 3: Save the trained model locally
    # Ensure the model directory exists
    os.makedirs(model_directory, exist_ok=True)
    
    # Construct the model filename using the DataFrame variable name
    model_filename = f'{name}_synthesizer.pkl'
    model_file_path = os.path.join(model_directory, model_filename)
    
    with open(model_file_path, 'wb') as file:
        pickle.dump(synthesizer, file)
    
    print(f"Model saved to {model_file_path}")
    return synthesizer

# Example usage:
# Assuming df_bass is your DataFrame
# metadata = generate_metadata(df_bass)  # Generate or load your metadata
# train_and_save_synthesizer(df_bass, metadata)


## Create Synthesizers for !Entire Labels!

In [ ]:
# Get unique values from the 'genre' and 'sound_type' columns
genres = df['genre'].unique()
sound_types = df['sound_type'].unique()

c_genre = []
c_sound_types = []

for genre in genres:
    temp = genre.replace('/', 'and')
    c_genre.append(temp)

for sound_type in sound_types:
    temp = sound_type.replace('/', 'and')
    c_sound_types.append(temp)

# Process each genre
for genre in c_genre:
    # Filter the DataFrame for the current genre
    genre_df = df[df['genre'] == genre]

    # Generate metadata for the current genre DataFrame
    metadata = generate_metadata(genre_df, genre)

    # Train and save synthesizer for the current genre DataFrame
    train_and_save_synthesizer(genre_df, metadata, genre)

# Process each sound type
for sound_type in c_sound_types:
    # Filter the DataFrame for the current sound type
    sound_type_df = df[df['sound_type'] == sound_type]

    # Generate metadata for the current sound type DataFrame
    metadata = generate_metadata(sound_type_df, sound_type)

    # Train and save synthesizer for the current sound type DataFrame
    train_and_save_synthesizer(sound_type_df, metadata, sound_type)

print("Synthesizers for all genres and sound types have been created and saved.")

In [192]:
import glob

folder_path = r'C:\Users\SKT012\project\data\models'
pkl_files = glob.glob(os.path.join(folder_path, '*.pkl'))

for file in pkl_files:
    # Extract the file name without extension
    synth = pd.read_pickle(file)
    file_name = os.path.basename(file).split('.')[0]
    out_dir = create_output_folder(file_name)
    working_df = preset_synthesis(synth, 10)
    post_processing(out_dir, working_df)


Saved C:\Users\SKT012\project\data\presets_synthesized\trained_synthesizer\AIU_Preset_1.json
Saved C:\Users\SKT012\project\data\presets_synthesized\trained_synthesizer\AIU_Preset_2.json
Saved C:\Users\SKT012\project\data\presets_synthesized\trained_synthesizer\AIU_Preset_3.json
Saved C:\Users\SKT012\project\data\presets_synthesized\trained_synthesizer\AIU_Preset_4.json
Saved C:\Users\SKT012\project\data\presets_synthesized\trained_synthesizer\AIU_Preset_5.json
Saved C:\Users\SKT012\project\data\presets_synthesized\trained_synthesizer\AIU_Preset_6.json
Saved C:\Users\SKT012\project\data\presets_synthesized\trained_synthesizer\AIU_Preset_7.json
Saved C:\Users\SKT012\project\data\presets_synthesized\trained_synthesizer\AIU_Preset_8.json
Saved C:\Users\SKT012\project\data\presets_synthesized\trained_synthesizer\AIU_Preset_9.json
Saved C:\Users\SKT012\project\data\presets_synthesized\trained_synthesizer\AIU_Preset_10.json


## Synthesizing Presets

In [147]:
# preset synthesis

def preset_synthesis(synthesizer, gen_num):
    gen_df = synthesizer.sample(num_rows=gen_num)
    return gen_df

In [150]:
def create_output_folder(name):    
    # Full path to the new folder
    output_preset_dir = os.path.join(output_directory, name)
    # Create the new folder
    os.makedirs(output_preset_dir, exist_ok=True)
    return output_preset_dir

## Postprocessing (실패, 아래에 있음) (X)

In [148]:
# Data

valid_wavetables_names = [
    "Init", "Basic Shapes", "Brown Noise", "Classic Blend", "Classic Fade", "Harmonic Series", "Pink Noise",
    "Pulse Width", "Quad Saw", "Three Graces", "White Noise", "Drink the Juice", "Low High Fold",
    "Post Modern Pulse", "Saws for Days", "Stabbed", "Vital Sine 2", "Vital Sine", "Didg", "Jaw Harp",
    "Acid Rock ft Maynix", "Additive Squish 2", "Alternating Harmonics", "Clicky Robot", "Corpusbode Phaser",
    "Crappy Toilet", "Creepy Solar", "Flange Sqrowl", "Granular Upgrade", "Hollow Distorted FM", "Solar Powered",
    "Squish Flange", "Thank u False Noise", "Water Razor",
    "Analog_BD_Sin" #외부 파형 중 개수 그나마 많은거 1개 추가
]

valid_sample_names = [
    'BART', 'Box Fan', 'Grinder', 'HVAC Unit', 'Jack Hammer',
    'River', 'Waves', 'Brown Noise', 'Pink Noise', 'White Noise',
    "BrightWhite", "Cassette Bell C Low", "3osc Noise" #외부 샘플 중 개수 그나마 많은거 3개 추가
]

wavetables = 'full_samples_and_wavetables(240812).json'
default = 'default_values.json'
samples_wavetables_path = os.path.join(data_directory, wavetables)
default_path = os.path.join(data_directory, default)

# Load the JSON file that contains the full samples and wavetables data
with open(samples_wavetables_path, 'r') as file:
    full_data = json.load(file)

full_sample_dict = full_data.get("full samples", {})
full_wavetables_dict = full_data.get("full wavetable", {})

with open(default_path, 'r') as default_file:
    default_values = json.load(default_file)



In [149]:
def postprocessing(df, name):
    output_dir = create_output_folder(name)
    process_dataframe(df)
    unflatten_and_save_json(df, output_dir, base_filename="AIU_Preset")
    update_json_files_in_directory(output_dir)
    process_json_files_1(output_dir)
    process_json_files_2(output_dir)
    process_json_files_3(output_dir)
    replace_nan_in_json_files(output_dir)
    remove_empty_keys_from_json(output_dir)
    process_json_files_4(output_dir)
    process_json_files_5(output_dir)
    process_json_files_6(output_dir)
    process_json_files_7(output_dir)
    process_json_files_8(output_dir)
    replace_empty_lfo_points(output_dir)
    update_json_files_with_defaults(output_dir)
    rename_json_to_vital(output_dir)
    change_extension_to_vital(output_dir)

In [151]:
# 불완전한 xy좌표 삭제, 오른쪽의 x좌표가 왼쪽의 x좌표보다 작으면 오른쪽 xy좌표 삭제

def process_dataframe(df):

    def process_group(group):
        # Separate X and Y pairs
        x_cols = group.columns[::2]
        y_cols = group.columns[1::2]
        
        new_data = []
        
        for idx, row in group.iterrows():
            # Extract X and Y values
            xy_pairs = [(row[x], row[y]) for x, y in zip(x_cols, y_cols)]
            
            # Remove pairs where either X or Y is NaN
            valid_pairs = [(x, y) for x, y in xy_pairs if not (np.isnan(x) or np.isnan(y))]
            
            # Compare X values and remove the right one if it's smaller than the left one
            filtered_pairs = []
            for i in range(len(valid_pairs)):
                if i == 0 or valid_pairs[i][0] >= valid_pairs[i - 1][0]:
                    filtered_pairs.append(valid_pairs[i])
            
            # Fill the new row data
            new_row = [val for pair in filtered_pairs for val in pair]
            new_row.extend([np.nan] * ((len(xy_pairs) * 2) - len(new_row)))  # Pad with NaNs if needed
            
            new_data.append(new_row)
        
        # Reconstruct the group with the new filtered data
        new_df_group = pd.DataFrame(new_data, columns=group.columns, index=group.index)
        return new_df_group

    # Apply the processing function to each group in the DataFrame
    grouped = df.columns.str.extract(r'(.*?)-points-')[0]
    new_df_group = pd.DataFrame(index=df.index)
    
    for group_name in grouped.unique():
        group_cols = df.columns[grouped == group_name]
        new_df_group[group_cols] = process_group(df[group_cols])

In [152]:
def nested_dict():
    """Helper function to create a nested defaultdict of defaultdicts"""
    return defaultdict(nested_dict)

def unflatten_and_save_json(df, output_dir, base_filename="output"):
    # Create a directory named after the original DataFrame
    directory = output_dir
    
    # Ensure the directory exists
    if not os.path.exists(directory):
        os.makedirs(directory)
    
    for idx, row in df.iterrows():
        # Create a nested dictionary
        root = nested_dict()
        
        for col, val in row.items():
            keys = col.split('--')
            d = root
            for key in keys[:-1]:
                d = d[key]
            d[keys[-1]] = val
        
        # Convert defaultdict to regular dict
        json_obj = json.loads(json.dumps(root))
        
        # Define filename
        filename = os.path.join(directory, f"{base_filename}_{idx}.json")
        
        # Save JSON object to file
        with open(filename, 'w') as f:
            json.dump(json_obj, f, indent=4)
        
        # Confirmation print
        print(f"Saved {filename}")

# Example usage:
# Assuming you have 'new_df' DataFrame ready
# unflatten_and_save_json(new_df, base_filename="AIU_Preset")


In [153]:
# 'author', 'comments', 'macro1', 'macro2', 'macro3', 'macro4' 복원

def update_json_files_in_directory(directory):
    starting_fields = {
    "author": "AIU",
    "comments": "FLY AI Challenger",
    "macro1": "MACRO 1",
    "macro2": "MACRO 2",
    "macro3": "MACRO 3",
    "macro4": "MACRO 4"
    }

    ending_field = {"synth_version": "1.5.5"}
    
    # Iterate over all files in the directory
    for filename in os.listdir(directory):
        if filename.endswith('.json'):
            file_path = os.path.join(directory, filename)

            # Read the current content of the JSON file
            with open(file_path, 'r') as file:
                data = json.load(file)

            # Insert the starting fields at the beginning of the JSON content
            updated_data = {**starting_fields, **data}

            # Add the ending field at the end of the JSON content
            updated_data.update(ending_field)

            # Write the updated content back to the JSON file
            with open(file_path, 'w') as file:
                json.dump(updated_data, file, indent=4)

    print(f"Updated JSON files in {directory}.")

In [154]:
#JSON Array 형식 복원

def unflatten_json(data):
    """
    Recursively unflatten the JSON object by converting numeric keys into list elements.
    """
    if isinstance(data, dict):
        numeric_keys = [key for key in data.keys() if key.isdigit()]
        if numeric_keys:
            # Sort numeric keys to preserve order in the list
            numeric_keys.sort(key=int)
            return [unflatten_json(data[key]) for key in numeric_keys]
        else:
            # Recursively apply unflattening to nested dictionaries
            return {key: unflatten_json(value) for key, value in data.items()}
    elif isinstance(data, list):
        # Recursively apply unflattening to lists
        return [unflatten_json(item) for item in data]
    else:
        return data

def process_json_file_0(file_path):
    """
    Load a JSON file, unflatten the data if necessary, and save the corrected data.
    """
    with open(file_path, 'r') as file:
        data = json.load(file)

    unflattened_data = unflatten_json(data)

    with open(file_path, 'w') as file:
        json.dump(unflattened_data, file, indent=4)

def process_json_files_1(directory):
    """
    Process all JSON files in the specified directory.
    """
    for filename in os.listdir(directory):
        if filename.endswith(".json"):
            file_path = os.path.join(directory, filename)
            process_json_file(file_path)

In [155]:
# points, powers에서 NaN 모두 삭제 (수정 필요??)

def clean_nans_in_arrays(data):
    if isinstance(data, dict):
        for key, value in data.items():
            if key in ["points", "powers"] and isinstance(value, list):
                data[key] = [x for x in value if not (isinstance(x, float) and math.isnan(x))]
            else:
                clean_nans_in_arrays(value)
    elif isinstance(data, list):
        for item in data:
            clean_nans_in_arrays(item)

def process_json_files_2(directory):
    for filename in os.listdir(directory):
        if filename.endswith('.json'):
            file_path = os.path.join(directory, filename)
            with open(file_path, 'r') as file:
                data = json.load(file)

            clean_nans_in_arrays(data)

            with open(file_path, 'w') as file:
                json.dump(data, file, indent=4)

In [156]:
# points가 비어있으면 parent object 삭제(settings-lfos 제외하고)

def clean_points_and_remove_empty_parents(data):
    if isinstance(data, dict):
        keys_to_delete = []
        for key, value in data.items():
            if isinstance(value, dict):
                clean_points_and_remove_empty_parents(value)
                # Special handling for "points" key within the nested dictionary
                if "points" in value and isinstance(value["points"], list) and len(value["points"]) <= 1:
                    # Mark the entire parent key for deletion
                    keys_to_delete.append(key)

            elif isinstance(value, list):
                # Clean nested lists
                clean_points_and_remove_empty_parents(value)

        # Remove the identified parent keys if "points" was empty or had one item
        for key in keys_to_delete:
            del data[key]

    elif isinstance(data, list):
        items_to_delete = []
        for i, item in enumerate(data):
            if isinstance(item, dict):
                # Avoid deletion if the parent key is "lfos"
                if "points" in item and isinstance(item["points"], list) and len(item["points"]) <= 1 and not math.isnan(item.get("name", 0)):
                    # Mark the entire object for deletion
                    items_to_delete.append(i)
                else:
                    clean_points_and_remove_empty_parents(item)

        # Remove the identified items from the list in reverse order to avoid index shifting
        for i in reversed(items_to_delete):
            del data[i]

def process_json_files_3(directory):
    for root, dirs, files in os.walk(directory):
        # Skip the lfos directory nested inside the settings directory
        if 'settings/lfos' in root or 'settings\\lfos' in root:  # Account for different OS path separators
            continue

        for filename in files:
            if filename.endswith('.json'):
                file_path = os.path.join(root, filename)
                with open(file_path, 'r') as file:
                    data = json.load(file)

                clean_points_and_remove_empty_parents(data)

                with open(file_path, 'w') as file:
                    json.dump(data, file, indent=4)

In [157]:
# NaN 모두 ""로 변경

def replace_nan_in_json_files(directory):
    def replace_nan_with_empty_string(data):
        if isinstance(data, dict):
            return {key: replace_nan_with_empty_string(value) for key, value in data.items()}
        elif isinstance(data, list):
            return [replace_nan_with_empty_string(item) for item in data]
        elif isinstance(data, float) and np.isnan(data):
            return ""
        else:
            return data

    # Iterate through all files in the directory
    for filename in os.listdir(directory):
        if filename.endswith('.json'):
            file_path = os.path.join(directory, filename)

            # Read the JSON file
            with open(file_path, 'r', encoding='utf-8') as file:
                json_data = json.load(file)

            # Replace NaN values
            updated_data = replace_nan_with_empty_string(json_data)

            # Write the updated JSON data back to the file
            with open(file_path, 'w', encoding='utf-8') as file:
                json.dump(updated_data, file, ensure_ascii=False, indent=4)

            print(f"Processed file: {file_path}")


In [158]:
# spectral_morph_phase 값 ""일 경우 삭제

def remove_empty_keys_from_json(directory):

    keys_to_check = ["osc_1_spectral_morph_phase", "osc_2_spectral_morph_phase", "osc_3_spectral_morph_phase"]

    # Iterate over all files in the directory
    for filename in os.listdir(directory):
        if filename.endswith(".json"):
            file_path = os.path.join(directory, filename)

            # Open the JSON file
            with open(file_path, 'r', encoding='utf-8') as f:
                data = json.load(f)

            # Check if 'settings' is in the JSON and it's a dictionary
            if 'settings' in data and isinstance(data['settings'], dict):
                # Check each key and delete if the value is an empty string
                for key in keys_to_check:
                    if key in data['settings'] and data['settings'][key] == "":
                        del data['settings'][key]

                # Save the modified JSON back to the file
                with open(file_path, 'w', encoding='utf-8') as f:
                    json.dump(data, f, indent=4)

                print(f"Processed file: {file_path}")




In [159]:
# points, num_points, powers 최소 규칙 맞추기(생성된거 보고 다시 작업하기)

def adjust_points_and_powers(data):
    if isinstance(data, dict):
        for key, value in data.items():
            if key == "points" and isinstance(value, list):
                # Ensure the number of points is even
                if len(value) % 2 != 0:
                    value.pop()  # Remove the last element if odd
                data['num_points'] = len(value) // 2

            if key == "powers" and isinstance(value, list) and 'num_points' in data:
                # Trim powers to match num_points
                data[key] = value[:data['num_points']]

            adjust_points_and_powers(value)
    elif isinstance(data, list):
        for item in data:
            adjust_points_and_powers(item)

def process_json_files_4(gen_dir):
    for filename in os.listdir(gen_dir):
        if filename.endswith('.json'):
            file_path = os.path.join(gen_dir, filename)
            with open(file_path, 'r') as file:
                data = json.load(file)

            adjust_points_and_powers(data)

            with open(file_path, 'w') as file:
                json.dump(data, file, indent=4)



In [160]:
def process_json_files_5(directory):
    # Iterate over all files in the directory
    for filename in os.listdir(directory):
        if filename.endswith('.json'):
            file_path = os.path.join(directory, filename)

            # Open and load the JSON file
            with open(file_path, 'r', encoding='utf-8') as file:
                data = json.load(file)

            # Process the modulations array
            if 'modulations' in data.get('settings', {}):
                data['settings']['modulations'] = [
                    modulation for modulation in data['settings']['modulations']
                    if modulation.get('destination') and modulation.get('source')
                ]

            # Modify the 'random_values' list by removing items with an empty 'seed'
            if 'random_values' in data.get('settings', {}):
                data['settings']['random_values'] = [
                    rv for rv in data['settings']['random_values']
                    if rv.get('seed') != ""
                ]

            # Save the modified JSON back to the file
            with open(file_path, 'w', encoding='utf-8') as file:
                json.dump(data, file, indent=4)

            print(f"Processed file: {file_path}")


In [161]:
# smooth 값 ""면 모두 false로 만들기 (원본 데이터셋에서 "true"보다 훨씬 비율 높음)

def replace_smooth_key(obj):
    """Recursively replace 'smooth' key's empty string values with False."""
    if isinstance(obj, dict):
        for key, value in obj.items():
            if key == "smooth" and value == "":
                obj[key] = False
            else:
                replace_smooth_key(value)
    elif isinstance(obj, list):
        for item in obj:
            replace_smooth_key(item)

def process_json_files_6(directory):
    """Process all JSON files in the given directory."""
    for filename in os.listdir(directory):
        if filename.endswith(".json"):
            file_path = os.path.join(directory, filename)
            with open(file_path, 'r') as file:
                data = json.load(file)

            replace_smooth_key(data)

            with open(file_path, 'w') as file:
                json.dump(data, file, indent=4)



In [162]:
# 마이너한 sample은 white noise로, 마이너한 wavetable은 init으로 name값 변경

def modify_json_structure(obj):
    """Recursively search and modify the 'name' keys in 'wavetables' and 'sample-name'."""
    if isinstance(obj, dict):
        for key, value in obj.items():
            if key == "wavetables" and isinstance(value, list):
                for wavetable in value:
                    if isinstance(wavetable, dict) and "name" in wavetable:
                        if wavetable["name"] not in valid_wavetables_names:
                            wavetable["name"] = "Init"
            elif key == "sample" and isinstance(value, dict) and "name" in value:
                if value["name"] not in valid_sample_names:
                    value["name"] = "White Noise"
            else:
                modify_json_structure(value)
    elif isinstance(obj, list):
        for item in obj:
            modify_json_structure(item)

def process_json_files_7(directory):
    """Process all JSON files in the given directory."""
    for filename in os.listdir(directory):
        if filename.endswith(".json"):
            file_path = os.path.join(directory, filename)
            with open(file_path, 'r') as file:
                data = json.load(file)

            modify_json_structure(data)

            with open(file_path, 'w') as file:
                json.dump(data, file, indent=4)

In [163]:
# sample과 wavetable 풀버전으로 교체 (****풀버전 JSON파일 경로 지정해줄것, 노트북 맨위에 다운 링크 있음)

def replace_with_full_data(obj):
    """Recursively replace sample and wavetable names with full dictionaries."""
    if isinstance(obj, dict):
        for key, value in obj.items():
            if key == "sample" and isinstance(value, dict) and "name" in value:
                sample_name = value["name"]
                if sample_name in full_sample_dict:
                    obj["sample"] = full_sample_dict[sample_name]
            elif key == "wavetables" and isinstance(value, list):
                for i in range(len(value)):
                    if "name" in value[i]:
                        wavetable_name = value[i]["name"]
                        if wavetable_name in full_wavetables_dict:
                            value[i] = full_wavetables_dict[wavetable_name]
            else:
                replace_with_full_data(value)
    elif isinstance(obj, list):
        for item in obj:
            replace_with_full_data(item)

def process_json_files_8(directory):
    """Process all JSON files in the given directory."""
    for filename in os.listdir(directory):
        if filename.endswith(".json"):
            file_path = os.path.join(directory, filename)
            with open(file_path, 'r') as file:
                data = json.load(file)

            replace_with_full_data(data)

            with open(file_path, 'w') as file:
                json.dump(data, file, indent=4)




In [164]:
# points값이 없는 빈 lfos 기본형으로 대체

def replace_empty_lfo_points(directory):

    # Replacement structure for empty "points" arrays in "lfos"
    replacement_lfo = {
        "name": "Triangle",
        "num_points": 3,
        "points": [
            0.0,
            1.0,
            0.5,
            0.0,
            0.5,
            1.0
        ],
        "powers": [
            0.0,
            0.0,
            0.0
        ],
        "smooth": False
    }

    # Iterate over all files in the specified directory
    for filename in os.listdir(directory):
        if filename.endswith('.json'):
            file_path = os.path.join(directory, filename)

            # Load the JSON data
            with open(file_path, 'r', encoding='utf-8') as file:
                data = json.load(file)

            # Check and replace the LFOs with empty "points"
            if 'settings' in data and 'lfos' in data['settings']:
                updated = False
                for i, lfo in enumerate(data['settings']['lfos']):
                    if 'points' in lfo and not lfo['points']:
                        data['settings']['lfos'][i] = replacement_lfo
                        updated = True

                # If any LFO was updated, save the changes
                if updated:
                    with open(file_path, 'w', encoding='utf-8') as file:
                        json.dump(data, file, indent=4)

                print(f"Processed file: {file_path}")



In [165]:
# ""인 값들 찾아서 기본값으로 대체(*****파일 경로 지정해줄것, default_values.json 파일 맨 위의 링크에 있음)


def update_json_files_with_defaults(directory):
    # Function to update JSON with default values
    def update_json_with_defaults(json_data, defaults):
        for key, value in json_data.items():
            if isinstance(value, dict):  # Recursively update nested dictionaries
                json_data[key] = update_json_with_defaults(value, defaults.get(key, {}))
            elif value == "" and key in defaults:  # Replace empty string with default value
                json_data[key] = defaults[key]
        return json_data
    
    # Iterate over all JSON files in the specified directory
    for filename in os.listdir(directory):
        if filename.endswith('.json'):
            file_path = os.path.join(directory, filename)

            # Load the JSON file
            with open(file_path, 'r', encoding='utf-8') as json_file:
                data = json.load(json_file)

            # Update the JSON data with default values
            updated_data = update_json_with_defaults(data, default_values)

            # Save the updated JSON back to the file
            with open(file_path, 'w', encoding='utf-8') as json_file:
                json.dump(updated_data, json_file, indent=4)
            
            print(f"Processed file: {file_path}")




In [166]:
# 확장자 vital로 변환

def rename_json_to_vital(directory):
    
    # Iterate over all files in the directory
    for filename in os.listdir(directory):
        if filename.endswith('.json'):
            # Construct the full file path
            json_path = os.path.join(directory, filename)
            
            # Replace .json with .vital
            vital_filename = filename.replace('.json', '.vital')
            vital_path = os.path.join(directory, vital_filename)
            
            # Rename the file
            os.rename(json_path, vital_path)
            
            print(f"Renamed file: {json_path} to {vital_path}")



In [167]:
def change_extension_to_vital(directory):
    """
    Change the extension from .json to .vital for all files in the specified directory.
    
    Parameters:
    directory (str): The path to the directory containing the JSON files.
    
    Returns:
    None
    """
    # Iterate over all files in the directory
    for filename in os.listdir(directory):
        if filename.endswith('.json'):
            # Construct the full file path
            json_path = os.path.join(directory, filename)
            
            # Replace .json with .vital
            vital_filename = filename.replace('.json', '.vital')
            vital_path = os.path.join(directory, vital_filename)
            
            # Rename the file
            os.rename(json_path, vital_path)
    
    print(f"All .json files in {directory} have been renamed to .vital")

# Example usage:
# change_extension_to_vital(r'C:\path\to\your\json\directory')


## Test

In [188]:
df_pluck = sound_type_dfs['Bass']
pluck_model = generate_synthesizer(df_pluck, 'Bass_test')


Model training took 00:05:54 (hh:mm:ss)
Model saved to C:\Users\SKT012\project\data\models\Bass_test_synthesizer.pkl


In [189]:
# How to use 2
# Access the DataFrame for sound_type 'Bass' from the sound_type_dfs dictionary
df_bass = sound_type_dfs['Bass']

# Now filter df_bass for genre 'Dubstep'
df_bass_dubstep = df_bass[df_bass['genre'] == 'Dubstep']
test_model = generate_synthesizer(df_bass_dubstep, 'dubstep_test')

Model training took 00:02:05 (hh:mm:ss)
Model saved to C:\Users\SKT012\project\data\models\dubstep_test_synthesizer.pkl


In [178]:
new_df = preset_synthesis(pluck_model, 10)

In [179]:
new_df.to_csv(file_path, index=False)

In [181]:
test_2 = preset_synthesis(pluck_model, 5)

In [184]:
dir = r'C:\Users\SKT012\project\data\test3'
post_processing(dir, test_2)

Saved C:\Users\SKT012\project\data\test2\AIU_Preset_1.json
Saved C:\Users\SKT012\project\data\test2\AIU_Preset_2.json
Saved C:\Users\SKT012\project\data\test2\AIU_Preset_3.json
Saved C:\Users\SKT012\project\data\test2\AIU_Preset_4.json
Saved C:\Users\SKT012\project\data\test2\AIU_Preset_5.json


## Postprocessing (진짜)

In [183]:
def post_processing(gen_dir, new_df):
    # Function to process each group
    def process_group(group):
        # Separate X and Y pairs
        x_cols = group.columns[::2]
        y_cols = group.columns[1::2]

        new_data = []
        for idx, row in group.iterrows():
            # Extract X and Y values
            xy_pairs = [(row[x], row[y]) for x, y in zip(x_cols, y_cols)]

            # Remove pairs where either X or Y is NaN
            valid_pairs = [(x, y) for x, y in xy_pairs if not (np.isnan(x) or np.isnan(y))]

            # Compare X values and remove the right one if it's smaller than the left one
            filtered_pairs = []
            for i in range(len(valid_pairs)):
                if i == 0 or valid_pairs[i][0] >= valid_pairs[i - 1][0]:
                    filtered_pairs.append(valid_pairs[i])

            # Fill the new row data
            new_row = [val for pair in filtered_pairs for val in pair]
            new_row.extend([np.nan] * (len(xy_pairs) * 2 - len(new_row)))  # Pad with NaNs if needed

            new_data.append(new_row)

        # Reconstruct the group with the new filtered data
        new_df_group = pd.DataFrame(new_data, columns=group.columns, index=group.index)
        return new_df_group

    # Apply the processing function to each group in new_df
    grouped = new_df.columns.str.extract(r'(.*)-points-')[0]
    for group_name in grouped.unique():
        group_cols = new_df.columns[grouped == group_name]
        new_df[group_cols] = process_group(new_df[group_cols])
    def nested_dict():
        """Helper function to create a nested defaultdict of defaultdicts"""
        return defaultdict(nested_dict)

    def unflatten_and_save_json(df, directory, base_filename="output"):
        """Function to unflatten DataFrame and save JSON files to a directory"""

        # Ensure the directory exists
        if not os.path.exists(directory):
            os.makedirs(directory)

        for idx, row in df.iterrows():
            # Create a nested dictionary
            root = nested_dict()

            for col, val in row.items():
                keys = col.split('-')
                d = root
                for key in keys[:-1]:
                    d = d[key]
                d[keys[-1]] = val

            # Convert defaultdict to regular dict
            json_obj = json.loads(json.dumps(root))

            # Define filename
            filename = os.path.join(directory, f"{base_filename}_{idx + 1}.json")

            # Save JSON object to file
            with open(filename, 'w') as f:
                json.dump(json_obj, f, indent=4)

            # Confirmation print
            print(f"Saved {filename}")

    # Example usage
    # Assuming you have `new_df` DataFrame ready
    unflatten_and_save_json(new_df, gen_dir, base_filename="AIU_Preset")

    # Fields to add at the beginning of the JSON
    starting_fields = {
        "author": "AIU",
        "comments": "FLY AI Challenger",
        "macro1": "MACRO 1",
        "macro2": "MACRO 2",
        "macro3": "MACRO 3",
        "macro4": "MACRO 4"
    }

    # Field to add at the end of the JSON
    ending_field = {"synth_version": "1.5.5"}

    # Iterate over all files in the directory
    for filename in os.listdir(gen_dir):
        if filename.endswith('.json'):
            file_path = os.path.join(gen_dir, filename)

            # Read the current content of the JSON file
            with open(file_path, 'r') as file:
                data = json.load(file)

            # Insert the starting fields at the beginning of the JSON content
            updated_data = {**starting_fields, **data}

            # Add the ending field at the end of the JSON content
            updated_data.update(ending_field)

            # Write the updated content back to the JSON file
            with open(file_path, 'w') as file:
                json.dump(updated_data, file, indent=4)

    def unflatten_json(data):
        """
        Recursively unflatten the JSON object by converting numeric keys into list elements.
        """
        if isinstance(data, dict):
            numeric_keys = [key for key in data.keys() if key.isdigit()]
            if numeric_keys:
                # Sort numeric keys to preserve order in the list
                numeric_keys.sort(key=int)
                return [unflatten_json(data[key]) for key in numeric_keys]
            else:
                # Recursively apply unflattening to nested dictionaries
                return {key: unflatten_json(value) for key, value in data.items()}
        elif isinstance(data, list):
            # Recursively apply unflattening to lists
            return [unflatten_json(item) for item in data]
        else:
            return data

    def process_json_file(file_path):
        """
        Load a JSON file, unflatten the data if necessary, and save the corrected data.
        """
        with open(file_path, 'r') as file:
            data = json.load(file)

        unflattened_data = unflatten_json(data)

        with open(file_path, 'w') as file:
            json.dump(unflattened_data, file, indent=4)

    def process_json_files_in_directory(directory):
        """
        Process all JSON files in the specified directory.
        """
        for filename in os.listdir(directory):
            if filename.endswith(".json"):
                file_path = os.path.join(directory, filename)
                process_json_file(file_path)



    # Process all JSON files in the directory
    process_json_files_in_directory(gen_dir)

    def clean_nans_in_arrays(data):
        if isinstance(data, dict):
            for key, value in data.items():
                if key in ["points", "powers"] and isinstance(value, list):
                    data[key] = [x for x in value if not (isinstance(x, float) and math.isnan(x))]
                else:
                    clean_nans_in_arrays(value)
        elif isinstance(data, list):
            for item in data:
                clean_nans_in_arrays(item)

    def process_json_files(directory):
        for filename in os.listdir(directory):
            if filename.endswith('.json'):
                file_path = os.path.join(directory, filename)
                with open(file_path, 'r') as file:
                    data = json.load(file)

                clean_nans_in_arrays(data)

                with open(file_path, 'w') as file:
                    json.dump(data, file, indent=4)


    process_json_files(gen_dir)

    def clean_points_and_remove_empty_parents(data):
        if isinstance(data, dict):
            keys_to_delete = []
            for key, value in data.items():
                if isinstance(value, dict):
                    clean_points_and_remove_empty_parents(value)
                    # Special handling for "points" key within the nested dictionary
                    if "points" in value and isinstance(value["points"], list) and len(value["points"]) <= 1:
                        # Mark the entire parent key for deletion
                        keys_to_delete.append(key)

                elif isinstance(value, list):
                    # Clean nested lists
                    clean_points_and_remove_empty_parents(value)

            # Remove the identified parent keys if "points" was empty or had one item
            for key in keys_to_delete:
                del data[key]

        elif isinstance(data, list):
            items_to_delete = []
            for i, item in enumerate(data):
                if isinstance(item, dict):
                    # Avoid deletion if the parent key is "lfos"
                    if "points" in item and isinstance(item["points"], list) and len(item["points"]) <= 1 and not math.isnan(item.get("name", 0)):
                        # Mark the entire object for deletion
                        items_to_delete.append(i)
                    else:
                        clean_points_and_remove_empty_parents(item)

            # Remove the identified items from the list in reverse order to avoid index shifting
            for i in reversed(items_to_delete):
                del data[i]

    def process_json_files(directory):
        for root, dirs, files in os.walk(directory):
            # Skip the lfos directory nested inside the settings directory
            if 'settings/lfos' in root or 'settings\\lfos' in root:  # Account for different OS path separators
                continue

            for filename in files:
                if filename.endswith('.json'):
                    file_path = os.path.join(root, filename)
                    with open(file_path, 'r') as file:
                        data = json.load(file)

                    clean_points_and_remove_empty_parents(data)

                    with open(file_path, 'w') as file:
                        json.dump(data, file, indent=4)

    # Replace 'gen_dir' with the actual directory you want to process
    process_json_files(gen_dir)

    # Function to replace NaN with empty string in JSON data
    def replace_nan_with_empty_string(data):
        if isinstance(data, dict):
            return {key: replace_nan_with_empty_string(value) for key, value in data.items()}
        elif isinstance(data, list):
            return [replace_nan_with_empty_string(item) for item in data]
        elif isinstance(data, float) and np.isnan(data):
            return ""
        else:
            return data

    # Iterate through all files in the gen_dir
    for filename in os.listdir(gen_dir):
        if filename.endswith('.json'):
            file_path = os.path.join(gen_dir, filename)

            # Read the JSON file
            with open(file_path, 'r', encoding='utf-8') as file:
                json_data = json.load(file)

            # Replace NaN values
            updated_data = replace_nan_with_empty_string(json_data)

            # Write the updated JSON data back to the file
            with open(file_path, 'w', encoding='utf-8') as file:
                json.dump(updated_data, file, ensure_ascii=False, indent=4)

    # Define the keys to check
    keys_to_check = ["osc_1_spectral_morph_phase",
                    "osc_2_spectral_morph_phase",
                    "osc_3_spectral_morph_phase"]

    # Iterate over all files in the directory
    for filename in os.listdir(gen_dir):
        if filename.endswith(".json"):
            file_path = os.path.join(gen_dir, filename)

            # Open the JSON file
            with open(file_path, 'r') as f:
                data = json.load(f)

            # Check if 'settings' is in the JSON and it's a dictionary
            if 'settings' in data and isinstance(data['settings'], dict):
                # Check each key and delete if the value is an empty string
                for key in keys_to_check:
                    if key in data['settings'] and data['settings'][key] == "":
                        del data['settings'][key]

            # Save the modified JSON back to the file
            with open(file_path, 'w') as f:
                json.dump(data, f, indent=4)

    def adjust_points_and_powers(data):
        if isinstance(data, dict):
            for key, value in data.items():
                if key == "points" and isinstance(value, list):
                    # Ensure the number of points is even
                    if len(value) % 2 != 0:
                        value.pop()  # Remove the last element if odd
                    data['num_points'] = len(value) // 2

                if key == "powers" and isinstance(value, list) and 'num_points' in data:
                    # Trim powers to match num_points
                    data[key] = value[:data['num_points']]

                adjust_points_and_powers(value)
        elif isinstance(data, list):
            for item in data:
                adjust_points_and_powers(item)

    def process_json_files(gen_dir):
        for filename in os.listdir(gen_dir):
            if filename.endswith('.json'):
                file_path = os.path.join(gen_dir, filename)
                with open(file_path, 'r') as file:
                    data = json.load(file)

                adjust_points_and_powers(data)

                with open(file_path, 'w') as file:
                    json.dump(data, file, indent=4)


    process_json_files(gen_dir)
    # Iterate over all files in the directory
    for filename in os.listdir(gen_dir):
        if filename.endswith(".json"):
            file_path = os.path.join(gen_dir, filename)

            # Open and load the JSON file
            with open(file_path, 'r') as file:
                data = json.load(file)

            # Process the modulations array
            if 'modulations' in data.get('settings', {}):
                data['settings']['modulations'] = [
                    modulation for modulation in data['settings']['modulations']
                    if modulation.get('destination') and modulation.get('source')
                ]

            # Save the modified JSON back to the file
            with open(file_path, 'w') as file:
                json.dump(data, file, indent=4)
    # Iterate over all files in the directory
    for filename in os.listdir(gen_dir):
        if filename.endswith(".json"):
            file_path = os.path.join(gen_dir, filename)

            # Open and load the JSON file
            with open(file_path, 'r') as file:
                data = json.load(file)

            # Modify the 'random_values' list by removing items with an empty 'seed'
            data['settings']['random_values'] = [rv for rv in data['settings']['random_values'] if rv.get('seed') != ""]

            # Save the modified JSON back to the file
            with open(file_path, 'w') as file:
                json.dump(data, file, indent=4)
    def replace_smooth_key(obj):
        """Recursively replace 'smooth' key's empty string values with False."""
        if isinstance(obj, dict):
            for key, value in obj.items():
                if key == "smooth" and value == "":
                    obj[key] = False
                else:
                    replace_smooth_key(value)
        elif isinstance(obj, list):
            for item in obj:
                replace_smooth_key(item)

    def process_json_files(directory):
        """Process all JSON files in the given directory."""
        for filename in os.listdir(directory):
            if filename.endswith(".json"):
                file_path = os.path.join(directory, filename)
                with open(file_path, 'r') as file:
                    data = json.load(file)

                replace_smooth_key(data)

                with open(file_path, 'w') as file:
                    json.dump(data, file, indent=4)


    process_json_files(gen_dir)

    valid_wavetables_names = [
        "Init", "Basic Shapes", "Brown Noise", "Classic Blend", "Classic Fade", "Harmonic Series", "Pink Noise",
        "Pulse Width", "Quad Saw", "Three Graces", "White Noise", "Drink the Juice", "Low High Fold",
        "Post Modern Pulse", "Saws for Days", "Stabbed", "Vital Sine 2", "Vital Sine", "Didg", "Jaw Harp",
        "Acid Rock ft Maynix", "Additive Squish 2", "Alternating Harmonics", "Clicky Robot", "Corpusbode Phaser",
        "Crappy Toilet", "Creepy Solar", "Flange Sqrowl", "Granular Upgrade", "Hollow Distorted FM", "Solar Powered",
        "Squish Flange", "Thank u False Noise", "Water Razor",
        "Analog_BD_Sin" #외부 파형 중 개수 그나마 많은거 1개 추가
    ]

    valid_sample_names = [
        'BART', 'Box Fan', 'Grinder', 'HVAC Unit', 'Jack Hammer',
        'River', 'Waves', 'Brown Noise', 'Pink Noise', 'White Noise',
        "BrightWhite", "Cassette Bell C Low", "3osc Noise" #외부 샘플 중 개수 그나마 많은거 3개 추가
    ]


    def modify_json_structure(obj):
        """Recursively search and modify the 'name' keys in 'wavetables' and 'sample-name'."""
        if isinstance(obj, dict):
            for key, value in obj.items():
                if key == "wavetables" and isinstance(value, list):
                    for wavetable in value:
                        if isinstance(wavetable, dict) and "name" in wavetable:
                            if wavetable["name"] not in valid_wavetables_names:
                                wavetable["name"] = "Init"
                elif key == "sample" and isinstance(value, dict) and "name" in value:
                    if value["name"] not in valid_sample_names:
                        value["name"] = "White Noise"
                else:
                    modify_json_structure(value)
        elif isinstance(obj, list):
            for item in obj:
                modify_json_structure(item)

    def process_json_files(directory):
        """Process all JSON files in the given directory."""
        for filename in os.listdir(directory):
            if filename.endswith(".json"):
                file_path = os.path.join(directory, filename)
                with open(file_path, 'r') as file:
                    data = json.load(file)

                modify_json_structure(data)

                with open(file_path, 'w') as file:
                    json.dump(data, file, indent=4)


    # Replace 'gen_dir' with the actual directory containing the JSON files
    process_json_files(gen_dir)

    # Load the JSON file that contains the full samples and wavetables data
    with open(samples_wavetables_path, 'r') as file:
        full_data = json.load(file)

    full_sample_dict = full_data.get("full samples", {})
    full_wavetables_dict = full_data.get("full wavetable", {})

    def replace_with_full_data(obj):
        """Recursively replace sample and wavetable names with full dictionaries."""
        if isinstance(obj, dict):
            for key, value in obj.items():
                if key == "sample" and isinstance(value, dict) and "name" in value:
                    sample_name = value["name"]
                    if sample_name in full_sample_dict:
                        obj["sample"] = full_sample_dict[sample_name]
                elif key == "wavetables" and isinstance(value, list):
                    for i in range(len(value)):
                        if "name" in value[i]:
                            wavetable_name = value[i]["name"]
                            if wavetable_name in full_wavetables_dict:
                                value[i] = full_wavetables_dict[wavetable_name]
                else:
                    replace_with_full_data(value)
        elif isinstance(obj, list):
            for item in obj:
                replace_with_full_data(item)

    def process_json_files(directory):
        """Process all JSON files in the given directory."""
        for filename in os.listdir(directory):
            if filename.endswith(".json"):
                file_path = os.path.join(directory, filename)
                with open(file_path, 'r') as file:
                    data = json.load(file)

                replace_with_full_data(data)

                with open(file_path, 'w') as file:
                    json.dump(data, file, indent=4)

    # Set the directory path to your JSON files
    directory_path = gen_dir
    process_json_files(directory_path)

    # Replacement structure for empty "points" arrays in "lfos"
    replacement_lfo = {
        "name": "Triangle",
        "num_points": 3,
        "points": [
            0.0,
            1.0,
            0.5,
            0.0,
            1.0,
            1.0
        ],
        "powers": [
            0.0,
            0.0,
            0.0
        ],
        "smooth": False
    }

    # Iterate over all files in the specified directory
    for filename in os.listdir(gen_dir):
        if filename.endswith(".json"):
            file_path = os.path.join(gen_dir, filename)

            # Load the JSON data
            with open(file_path, 'r') as file:
                data = json.load(file)

            # Check and replace the LFOs with empty "points"
            if "settings" in data and "lfos" in data["settings"]:
                updated = False
                for i, lfo in enumerate(data["settings"]["lfos"]):
                    if "points" in lfo and not lfo["points"]:
                        data["settings"]["lfos"][i] = replacement_lfo
                        updated = True

                # If any LFO was updated, save the changes
                if updated:
                    with open(file_path, 'w') as file:
                        json.dump(data, file, indent=4)



    #        print(f"Processed {filename}")

    # Load default values from the provided file
    with open(default_values_path, 'r') as default_file:
        default_values = json.load(default_file)


    # Function to update JSON with default values
    def update_json_with_defaults(json_data, defaults):
        for key, value in json_data.items():
            if isinstance(value, dict):  # Recursively update nested dictionaries
                json_data[key] = update_json_with_defaults(value, defaults.get(key, {}))
            elif value == "" and key in defaults:
                json_data[key] = defaults[key]
        return json_data

    # Iterate over all JSON files in gen_dir
    for filename in os.listdir(gen_dir):
        if filename.endswith('.json'):
            file_path = os.path.join(gen_dir, filename)

            # Load the JSON file
            with open(file_path, 'r') as json_file:
                data = json.load(json_file)

            # Update the JSON data with default values
            updated_data = update_json_with_defaults(data, default_values)

            # Save the updated JSON back to the file
            with open(file_path, 'w') as json_file:
                json.dump(updated_data, json_file, indent=4)

    # Change the extension from .json to .vital for all files in gen_dir
    for filename in os.listdir(gen_dir):
        if filename.endswith('.json'):
            # Construct the full file path
            json_path = os.path.join(gen_dir, filename)
            # Replace .json with .vital
            vital_filename = filename.replace('.json', '.vital')
            vital_path = os.path.join(gen_dir, vital_filename)
            # Rename the file
            os.rename(json_path, vital_path)